In [1]:
import datajoint as dj
import importlib
importlib.reload(dj.blob)
import sys
sys.path.append('/Users/carlos/Github/UberPhys/src')

import numpy as np

import sys
import pickle
# sys.path.append('/Users/carlos/Github/UberPhys/src')
sys.path.append('/Users/carlos/Github/bl_pipeline_python')
import datajoint as dj
import utility.blob_transformation as bt
import os

import pandas as pd

dj.blob.use_32bit_dims = True  # necessary for pd.blob read

dj.config['database.host'] = 'datajoint01.pni.princeton.edu'
# dj.config['database.host'] = 'bdata00.pni.princeton.edu'
dj.config['database.user'] = 'brody'  # enter your puid username

dj.conn()

if dj.config['database.host'] != 'datajoint01.pni.princeton.edu':
    raise ValueError("Only run this on datajoint01.pni.princeton.edu")


[2024-06-08 13:56:21,858][INFO]: Connecting brody@datajoint01.pni.princeton.edu:3306
[2024-06-08 13:56:23,134][INFO]: Connected brody@datajoint01.pni.princeton.edu:3306


In [2]:
dj.conn()

DataJoint connection (connected) brody@datajoint01.pni.princeton.edu:3306

In [ ]:
dj.list_schemas()

In [ ]:
schema = dj.schema('bl_sandbox')

In [ ]:
schema.drop()

## Alvaro virtual module

In [ ]:
subjectSchema = dj.create_virtual_module('bl_subject', 'bl_subject')
dj.Diagram(subjectSchema)

In [ ]:
bdata = dj.create_virtual_module('bdata', 'bl_new_acquisition')

In [ ]:
dj.Diagram(bdata)

In [ ]:
g = (bdata.Sessions() & "session_rat = 'A327'" & "sessid = 845759").fetch(as_dict=True)[0]

In [ ]:
bdata.Sessions().insert1(g, replace=True)

In [ ]:
(bdata.Sessions() & "session_rat = 'A327'" & "sessid = 845759").fetch(as_dict=True)[0]

## Carlos schema

In [15]:
import datajoint as dj

dj.blob.use_32bit_dims = False  # necessary for pd.blob read-- but here will stay with 64-bit blob encoding

dj.config['database.host'] = 'datajoint01.pni.princeton.edu'
dj.config['database.user'] = 'brody'  # enter your puid username

dj.conn()


DataJoint connection (disconnected) brody@datajoint01.pni.princeton.edu:3306

In [16]:
schema = dj.schema('brody_test')

@schema
class BehaviorEvent(dj.Manual):
     definition = """
     #  Contains all data from parsed_events from all sessions
     sessid:                 INT(11)                    # Unique number for session
     id_event:               INT(11)                    # Unique number for event                      
     -----
     trial:                  INT(10)                    # trial number event occurred in
     event_type:             VARCHAR(16)                # type of event in session, one of (pokes, states, waves)
     event_name:             VARCHAR(32)                # sub category of event type (e.g. C, L, R, state0)
     entry_num:              INT(10)                    # occurence number of event inside trial -- e.g., the second C poke in a trial would have this as 2
     in_time=null:           DOUBLE                     # start time of event
     out_time=null:          DOUBLE                     # end time of event
     """


@schema
class Sessions(dj.Manual):
     definition = """
     sessid:                  INT(11)                   # Unique number for session                
     -----
     ratname:  varchar(30)
     hostname:  varchar(30)
     experimenter:  varchar(30)
     starttime:  time
     endtime:  time
     sessiondate:  date
     n_done_trials:  int(11)
     comments:  varchar(1000)
     settings_file:  varchar(200)
     settings_path:  varchar(200)
     data_file:  varchar(200)
     data_path:  varchar(200)
     video_file:  varchar(200)
     video_path:  varchar(200)
     protocol:  varchar(30)
     total_correct:  float(2,2)
     right_correct:  float(2,2)
     left_correct:  float(2,2)
     percent_violations:  float(2,2)
     brokenbits:  int(11)
     protocol_data:  mediumblob
     left_pokes:  int(10)
     center_pokes:  int(10)
     right_pokes:  int(10)
     technotes:  varchar(200)
     ip_addr:  varchar(15)
     crashed=0:  tinyint(1)
     foodpuck:  tinyint(1)
     """


@schema
class ParsedEvents(dj.Manual):
     definition = """
     sessid:                 INT(11)                    # Unique number for session
     -----
     peh:                    mediumblob                  # parsed events
     """




[2024-06-08 19:06:12,429][WARNING]: MySQL server has gone away. Reconnecting to the server.


In [ ]:
gu = dj.create_virtual_module('bl_sandbox', 'bl_sandbox')

In [ ]:
schema = dj.schema('bl_sandbox')

In [ ]:
schema.spawn_missing_classes()

In [ ]:
class BehaviorEvent4(dj.Manual):
    __doc__ = "Hmmm."


In [ ]:
BehaviorEvent4().__doc__

In [ ]:
gu.BehaviorEvent4.describe()

In [ ]:
schema.list_tables()

In [ ]:
print(BehaviorEvent4.__doc__)

In [ ]:
gu = np.array([10,20])
gu.__doc__

In [ ]:
print(BehaviorEvent4.describe())

In [ ]:
BehaviorEvent() & "sessid=845759" & "trial=2"

In [ ]:
BehaviorEvent() & "sessid=92722"

## Load pickled Sessions()

In [17]:
ratname = "A327"
fp = open("/Users/carlos/Github/bl_pipeline_python/carlos/%s_sessions.pkl" % ratname, "rb")
sessions = pickle.load(fp)
for i in range(len(sessions)):
    sessions[i]["ip_addr"] = sessions[i]["IP_addr"]
    del sessions[i]["IP_addr"]

    sessions[i]["protocol_data"] = bt.transform_blob(sessions[i]["protocol_data"])

sessids = np.array([s["sessid"] for s in sessions])

In [ ]:
def getProtocolData(sessid):
    u = np.argwhere(sessids == sessid)[0][0]
    return sessions[u]["protocol_data"]

def date2sessid(date):
    if isinstance(date, str):
        date = datetime.date(*[int(x) for x in date.split("-")])
    return np.array([s["sessid"] for s in sessions if s["sessiondate"] == date])

date2sessid(datetime.date(2023, 9, 1))
getProtocolData(date2sessid("2023-09-01")[0])



In [ ]:
date2sessid("2023-09-01")[0]
np.argwhere(sessids == 927222)[0][0]
sessions[479]["protocol_data"]

In [ ]:
import datetime
datetime.date(2023, 9, 1)

In [ ]:
ratname = "A327"
fp = open("/Users/carlos/Github/bl_pipeline_python/carlos/%s_sessions.pkl" % ratname, "rb")
sessions = pickle.load(fp)
sessions[0]

In [ ]:
df = Sessions().fetch("sessid", "sessiondate", "ratname", as_dict=True)

In [ ]:
df = pd.DataFrame(df)
df[['sessid', 'sessiondate']][-120:-1]


In [ ]:
df[["sessid", "sessiondate"]]

In [20]:
print(Sessions.describe())

sessid               : int                          # Unique number for session
---
ratname              : varchar(30)                  
hostname             : varchar(30)                  
experimenter         : varchar(30)                  
starttime            : time                         
endtime              : time                         
sessiondate          : date                         
n_done_trials        : int                          
comments             : varchar(1000)                
settings_file        : varchar(200)                 
settings_path        : varchar(200)                 
data_file            : varchar(200)                 
data_path            : varchar(200)                 
video_file           : varchar(200)                 
video_path           : varchar(200)                 
protocol             : varchar(30)                  
total_correct        : float(2,2)                   
right_correct        : float(2,2)                   
left_correct   

In [21]:
ratname = "A327"
fp = open("/Users/carlos/Github/bl_pipeline_python/carlos/%s_sessions.pkl" % ratname, "rb")
sessions = pickle.load(fp)
for i in range(len(sessions)):
    sessions[i]["ip_addr"] = sessions[i]["IP_addr"]
    del sessions[i]["IP_addr"]
    
    sessions[i]["protocol_data"] = bt.transform_blob(sessions[i]["protocol_data"])


for i in range(len(sessions)):
    if len(sessions[i]) == 0:  # if no events, skip session
        continue
    # existing = (Sessions & "sessid=%d" % sessions[i]["sessid"]).fetch("ratname")
    #if existing.size > 0:  # if session already exists, skip
    #    print("sessid=%d (i=%d/%d) already exists" % (sessions[i]["sessid"], i, len(sessions)))
    #    continue
    
    # Ok, insert this session:
    Sessions.insert([sessions[i]], replace=True)

    # report every now and then
    if i % 10 == 0:
        print("Inserted %d/%d sessions" % (i, len(sessions)))

Inserted 0/544 sessions
Inserted 10/544 sessions
Inserted 20/544 sessions
Inserted 30/544 sessions
Inserted 40/544 sessions
Inserted 50/544 sessions
Inserted 60/544 sessions
Inserted 70/544 sessions
Inserted 80/544 sessions
Inserted 90/544 sessions
Inserted 100/544 sessions
Inserted 110/544 sessions
Inserted 120/544 sessions
Inserted 130/544 sessions
Inserted 140/544 sessions
Inserted 150/544 sessions
Inserted 160/544 sessions
Inserted 170/544 sessions
Inserted 180/544 sessions
Inserted 190/544 sessions
Inserted 200/544 sessions
Inserted 210/544 sessions
Inserted 220/544 sessions
Inserted 230/544 sessions
Inserted 240/544 sessions
Inserted 250/544 sessions
Inserted 260/544 sessions
Inserted 270/544 sessions
Inserted 280/544 sessions
Inserted 290/544 sessions
Inserted 300/544 sessions
Inserted 310/544 sessions
Inserted 320/544 sessions
Inserted 330/544 sessions
Inserted 340/544 sessions
Inserted 350/544 sessions
Inserted 360/544 sessions
Inserted 370/544 sessions
Inserted 380/544 sessio

In [25]:
g = (Sessions() & "sessid=927222").fetch(as_dict=True)[0]
g["protocol_data"]

{'hits': array([[ 1.],
        [ 1.],
        [nan],
        [nan],
        [nan],
        [ 1.],
        [ 1.],
        [ 0.],
        [nan],
        [ 1.],
        [ 1.],
        [nan],
        [nan],
        [ 1.],
        [ 1.],
        [nan],
        [ 1.],
        [ 1.],
        [ 1.],
        [nan],
        [ 0.],
        [ 1.],
        [nan],
        [ 1.],
        [ 1.],
        [ 1.],
        [nan],
        [nan],
        [nan],
        [nan],
        [ 1.],
        [nan],
        [nan],
        [ 1.],
        [nan],
        [nan],
        [nan],
        [nan],
        [ 1.],
        [nan],
        [nan],
        [ 1.],
        [ 1.],
        [ 0.],
        [ 1.],
        [nan],
        [nan],
        [ 1.],
        [nan],
        [ 1.],
        [nan],
        [ 1.],
        [nan],
        [ 1.],
        [nan],
        [ 1.],
        [ 1.],
        [ 0.],
        [ 1.],
        [ 1.],
        [ 1.],
        [nan],
        [ 1.],
        [nan],
        [ 1.],
        [ 1.],
  

In [ ]:
(Sessions() & "sessid=%d" % sessions[1]["sessid"]).fetch("protocol_data")

In [ ]:
bt.transform_blob(sessions[i]["protocol_data"])

In [ ]:
BehaviorEvent()

## Load pickled BehaviorEvent()

In [ ]:
ratname = "A327"
fp = open("/Users/carlos/Github/bl_pipeline_python/carlos/%s_sessionsAndBevs.pkl" % ratname, "rb")
sessionsAndBevs = pickle.load(fp)


In [ ]:
sessionsAndBevs[0]

Safe to run, it'll only insert sessions that aren't already in there.

In [ ]:
ratname = "A327"
fp = open("/Users/carlos/Github/bl_pipeline_python/carlos/%s_sessionsAndBevs.pkl" % ratname, "rb")
sessionsAndBevs = pickle.load(fp)


for i in range(len(sessionsAndBevs)):
    if len(sessionsAndBevs[i]) == 0:  # if not events, skip session
        continue
    existing = (BehaviorEvent & "sessid=%d" % sessionsAndBevs[i][0]["sessid"]).fetch("id_event")
    if len(existing) > 0:  # if session already exists, skip
        print("sessid=%d (i=%d/%d) already exists" % (sessionsAndBevs[i][0]["sessid"], i, len(sessionsAndBevs)))
        continue
    
    # Ok, insert this session:
    BehaviorEvent.insert(sessionsAndBevs[i])

    # report every now and then
    if i % 10 == 0:
        print("Inserted %d/%d sessions" % (i, len(sessionsAndBevs)))

## Dataframe playing

In [ ]:
import pandas as pd

df = (BehaviorEvent() & "sessid=927222").fetch(format="frame")
df

In [ ]:
# Give me the wave names and their in times, sorted by in time, for trial 1:

df[(df.trial==1) & (df.event_type=="waves")].sort_values("in_time")[["event_name", "in_time", "out_time"]]

In [ ]:
import pandas as pd

# For each trial, give me the in times of the sound_on and play_stimulus_sound in_time events:
#
# Note that in some trials, the animal never poked, so those trial don't make it here. play_sound
# and sound_on are two different values of event_name in the original dataframe. The pivot_table 
# call here will create a new column for each unique value of event_name, and put the value of 
# in_time in that column.
# 
pd.pivot_table(df[(df.event_name=="sound_on") | (df.event_name=="play_stimulus_sound")], index="trial", values="in_time", columns=["event_name"]) 

In [ ]:
df.groupby("trial").count()

In [ ]:
df[df.trial==814].sort_values("in_time")

In [ ]:
df[(df.event_name=="sound_on") | (df.event_name=="play_stimulus_sound")].in_time

In [ ]:
df.groupby("event_name").nth(1)

In [ ]:
# Give me the state names and their in times, sorted by in time, for trial 1:

# df = (BehaviorEvent() & "sessid=927222").fetch(format="frame")

df[(df.trial==1) & (df.event_type=="states")].sort_values("in_time")[["event_name", "in_time", "out_time"]]

In [ ]:
# Give me the start time of each trial:

df[(df.event_name=="state_0") & (df.entry_num==1)].in_time.values

In [ ]:
def get_clicks_on(trialnum, bevFrame):
    """
    Given a trial number and a dataframe that contains the BehaviorEvents for a given session, 
    return the time at which the clicks began playing (i.e., time of stereo click)
    """

In [ ]:
df[["trial", "event_type"]].groupby("trial")

In [ ]:
mydf = pd.DataFrame([{"sessid": 1, "trial": 1, "event_type": "poke", "event_name": "L", "entry_num": 1, "in_time": 0.1, "out_time": 0.2}])
mydf.columns

In [ ]:
df.groupby("trial")

In [ ]:
Sessions() & "ratname='A327'" & "sessiondate='2023-09-01'"

In [ ]:
gu = (BehaviorEvent() & "sessid=%d" % sessionsAndBevs[1][0]["sessid"]).fetch(as_dict=True)

In [ ]:
gu = (BehaviorEvent() & "sessid=%d" % 23).fetch(as_dict=True)

In [ ]:
gu

In [ ]:
bdata = dj.create_virtual_module('bdata', 'bdata')

## Load pickled Parsed Events

In [9]:
ratname = "A327"
fp = open("/Users/carlos/Github/bl_pipeline_python/carlos/%s_parsed_events.pkl" % ratname, "rb")
parsed_events = pickle.load(fp)


In [10]:
print(ParsedEvents.describe())

sessid               : int                          # Unique number for session
---
peh                  : mediumblob                   # parsed events



In [11]:
for i in range(len(parsed_events)):
    if len(parsed_events[i]) == 0:  # if no events, skip entry
        continue
    if type(parsed_events[i]["peh"]) == dj.blob.MatStruct:
        parsed_events[i]["peh"] = bt.transform_blob(parsed_events[i]["peh"])

    # Ok, insert this session:
    ParsedEvents.insert([parsed_events[i]], replace=True)

    # report every now and then
    if i % 10 == 0:
        print("Inserted %d/%d sessions" % (i, len(parsed_events)))

Inserted 0/544 sessions
Inserted 10/544 sessions
Inserted 20/544 sessions
Inserted 30/544 sessions
Inserted 40/544 sessions
Inserted 50/544 sessions
Inserted 60/544 sessions
Inserted 70/544 sessions
Inserted 80/544 sessions
Inserted 90/544 sessions
Inserted 100/544 sessions
Inserted 110/544 sessions
Inserted 120/544 sessions
Inserted 130/544 sessions
Inserted 140/544 sessions
Inserted 150/544 sessions
Inserted 160/544 sessions
Inserted 170/544 sessions
Inserted 180/544 sessions
Inserted 190/544 sessions
Inserted 200/544 sessions
Inserted 210/544 sessions
Inserted 220/544 sessions
Inserted 230/544 sessions
Inserted 240/544 sessions
Inserted 250/544 sessions
Inserted 260/544 sessions
Inserted 270/544 sessions
Inserted 280/544 sessions
Inserted 290/544 sessions
Inserted 300/544 sessions
Inserted 310/544 sessions
Inserted 320/544 sessions
Inserted 330/544 sessions
Inserted 340/544 sessions
Inserted 350/544 sessions
Inserted 360/544 sessions
Inserted 370/544 sessions
Inserted 380/544 sessio

In [14]:
(ParsedEvents() & "sessid=927222").fetch("peh")[0]

[{'pokes': {'C': array([[917.809236, 918.34224 ],
          [918.414747, 918.550242],
          [918.62274 , 919.558236]]),
   'L': array([], shape=(0, 2), dtype=float64),
   'R': array([[916.179736, 916.205239],
          [916.486236, 916.598236],
          [916.63474 , 916.75224 ],
          [916.777236, 916.901736],
          [920.378248, 920.507736]]),
   'starting_state': {'C': 'out',
    'L': array([], shape=(0, 0), dtype=float64),
    'R': 'out'},
   'ending_state': {'C': 'out',
    'L': array([], shape=(0, 0), dtype=float64),
    'R': 'out'}},
  'waves': {'direct_left_reward': array([], shape=(0, 2), dtype=float64),
   'direct_right_reward': array([920.478746, 920.623736]),
   'mtime_since_cpoke': array([918.810741, 918.810741]),
   'laser_stim_on': array([], shape=(0, 2), dtype=float64),
   'mask_on': array([], shape=(0, 2), dtype=float64),
   'sound_on': array([918.336741, 919.311736]),
   'min_rt_wave': array([919.411243, 919.559236]),
   'cpoke_timer': array([919.312236, 91

In [5]:
ParsedEvents().fetch(as_dict=True)

[{'sessid': 845759,
  'peh': [{'pokes': {'C': array([], shape=(0, 2), dtype=float64),
     'L': array([[666.324904, 666.365404],
            [666.520504, 666.837604]]),
     'R': array([], shape=(0, 2), dtype=float64),
     'starting_state': {'C': array([], shape=(0, 0), dtype=float64),
      'L': 'out',
      'R': array([], shape=(0, 0), dtype=float64)},
     'ending_state': {'C': array([], shape=(0, 0), dtype=float64),
      'L': 'out',
      'R': array([], shape=(0, 0), dtype=float64)}},
    'waves': {'stim_wave': array([], shape=(0, 2), dtype=float64),
     'rew_wave': array([], shape=(0, 2), dtype=float64),
     'rew_big_wave': array([666.394604, 666.394704]),
     'memoryzap_wave': array([], shape=(0, 2), dtype=float64),
     'bad_nic_wave': array([], shape=(0, 2), dtype=float64),
     'noseincenter_wave': array([], shape=(0, 2), dtype=float64),
     'legalcbreak_wave': array([], shape=(0, 2), dtype=float64),
     'prestim_wave': array([], shape=(0, 2), dtype=float64),
     'endN

# Other stuff


In [ ]:
def matStruct2py(m, verbose=False):
    """
    This function takes a dj.blob.MatStruct object and returns a dictionary 
    with its contents of the Matlab file.

    Parameters
    ----------
    """

    def cellParse(m):
        """
        This function parses a cell array. It is called by singleLevelParse() and structureParse().
        For cell arrays with a single element, we'll try to unpack the content into a regular data type.
        For cell arrays with multiple elements, the different elements coule be different types, so
        they'll go into a numpy object array (dtype = np.object_) to allow for different data types.

        Parameters
        ----------
        m : np.array

        Returns
        -------
        res : np.array
            The parsed contents of the cell array.

        goodFlag : bool
            True if the parsing of all elements was successful, False otherwise.


        """
        if m.size == 1: # cell has only one element, we can return it as a regular data type if possible
            res, goodFlag = singleLevelParse(m.flat[0])
            if (not goodFlag) and verbose:
                print("Warning: singleLevelParse() returned with error when object to be parsed was ", m.flat[i])
            return res.squeeze()
        
        # else pack contents into a cell to allow different data types for different entries:    
        res = np.empty(m.shape, np.object_)
        for i in range(m.size):
            res.flat[i], goodFlag = singleLevelParse(m.flat[i])
            if (not goodFlag) and verbose:
                print("Warning: singleLevelParse() returned with error when object to be parsed was ", m.flat[i])
        return res.squeeze()


    def singleLevelParse(m):
        """
        This function parses a single element. It is called by cellParse() and structureParse(),
        and can in turn call them, to handle nested structures and cells.
        If the passed element has a data type with length greater than one, then 
        unless it is MatlabOpaque, it is a structure, so structureParse() is called to parse it.
        If its data type is a subtype of np.object_, then it is a cell array, 
        so cellParse() is called to parse it. Otherwise it is parsed as a regular data type, with
        attempts to unsqueeze as far as possible (e.g., a 1x1 array is converted to a scalar).

        Parameters
        ----------
        m : np.array

        Returns
        -------
        res : np.array
            The parsed contents of m.

        goodFlag : bool
            True if the parsing was successful, False otherwise.
        """
        goodFlag = True    
        if hasattr(m, 'dtype') and len(m.dtype)>1:
            if type(m) == scipy.io.matlab.MatlabOpaque:
                res = "Sorry, cannot parse a MatlabOpaque object"
                if verbose:
                    print("Warning: singleLevelParse() found a MatlabOpaque object")
                goodFlag = False
            else:
                res, goodFlag = structureParse(m)
                if (not goodFlag) and verbose:
                    print("Warning: structureParse() returned with error when object to be parsed was ", m)
        elif not hasattr(m, 'dtype'):
            res = None
            goodFlag = False
            if verbose:
                print("Warning: singleLevelParse() found no dtype attribute for entry ", m)
        elif np.issubdtype(m.dtype, np.object_):
            res = cellParse(m)
        elif np.issubdtype(m.dtype, np.integer) and m.size == 1:
            res = m[0,0].astype(int).squeeze()
        elif np.issubdtype(m.dtype, np.integer) and (m.size == 0 or m.size > 1):
            res = m.astype(int).squeeze()
        elif np.issubdtype(m.dtype, np.float_) and m.size == 1:
            res = m[0,0].astype(float).squeeze()
        elif np.issubdtype(m.dtype, np.float_) and (m.size == 0 or m.size > 1):
            res = m.astype(float).squeeze()
        elif np.issubdtype(m.dtype, np.float32) and m.size == 1:
            res = m[0,0].astype(np.float32).squeeze()
        elif np.issubdtype(m.dtype, np.float32) and (m.size == 0 or m.size > 1):
            res = m.astype(np.float32).squeeze()
        elif m.dtype.descr[0][1].startswith('<U') and m.size == 1:
            res = m[0].squeeze()
        elif m.dtype.descr[0][1].startswith('<U') and (m.size == 0 or m.size > 1):
            res = m.astype(str).squeeze()
        else:
            res = None
            if verbose:
                print("Warning: singleLevelParse() coudn't parse, it is missing a case for ", m)
            goodFlag = False

        return res, goodFlag


    def structureParse(m):
        """
        This function parses a structure. It is called by singleLevelParse().
        It returns a dictionary with the contents of the structure.

        Parameters
        ----------
        m : np.array

        Returns
        -------
        res : dict
            The parsed contents of the structure.
        """
        allGood = True
        res = {}
        z = m.dtype.names
        for n in range(len(z)):
            if len(m.shape)==1:
                msg = m[0][z[n]]
            elif len(m.shape)==2:
                msg = m[0,0][z[n]]
            else:
                # print("Warning: structureParse() found unexpected shape for entry ", k)
                raise ValueError("Unexpected shape for entry ", m)

            if hasattr(msg, 'dtype'):
                if len(msg.dtype)<=1:
                    res[z[n]], goodFlag = singleLevelParse(msg)
                    allGood = allGood and goodFlag
                    if (not goodFlag) and verbose:
                        print("singleLevelParse() just returned with error when msg was ", msg)
                else:   
                    if type(msg) == scipy.io.matlab.MatlabOpaque:
                        res[z[n]] = "Sorry, cannot parse a MatlabOpaque object"
                        if verbose:
                            print("Warning: singleLevelParse() found a MatlabOpaque object")
                        allGood = False
                    else:
                        res[z[n]], goodFlag = structureParse(msg)
                        allGood = allGood and goodFlag
                        if (not goodFlag) and verbose:
                            print("structure parse() just returned with error when msg was ", msg)
            else:
                if verbose:
                    print("structureParse(): Skipping ", z[n])
                allGood = False

        return res, allGood

    res = {}
    skipped = []
    for k, v in m.items():
        if not k.startswith("__"):
            if hasattr(m[k], 'dtype'):
                res[k], goodFlag = singleLevelParse(m[k])
                if (not goodFlag) and verbose:
                    print("Warning: singleLevelParse() returned with error at outer level when k was ", k)
            else:
                if verbose:
                    print("Outer level Skipping ", k)
                skipped.append[v]

    return res


In [ ]:
mysessid = 956289
gu = (bdata.ParsedEvents & "sessid = %d" % mysessid).fetch('peh', as_dict=True)[0]['peh']

In [ ]:
gaz = 2

def recArrayParsed(m):
    if m.size > 1:
        m = m.squeeze()

    names = m.dtype.names
    nNames = len(names)
    nEntries = m.size

    res = np.empty(nEntries, np.object_)

    for entry in range(nEntries):
        res[entry] = {} # the dict for this trial, with the names as keys
        for n in range(nNames):
            res[entry][names[n]] = {}
            z = m[entry][names[n]][0]
            if z.size > 0:
                z = z[0]
            innerNames = z.dtype.names
            if innerNames is None:
                if z.size == 1:
                    res[entry][names[n]] = z.item()
                else:
                    res[entry][names[n]] = z
                continue
            nInnerNames = len(innerNames)
            for k in range(nInnerNames):
                if type(z[innerNames[k]]) == dj.blob.MatStruct:
                    res[entry][names[n]][innerNames[k]] = recArrayParsed(z[innerNames[k]])
                else:   
                    res[entry][names[n]][innerNames[k]] = z[innerNames[k]].squeeze()

    if res.size == 1:
        return res.item()
    else:
        return res.squeeze()

In [ ]:
m0 = gu.squeeze()
z0 = m[1]["pokes"][0,0]["starting_state"]

z0[0]["L"][0].size

In [ ]:
z0

In [ ]:
recArrayParsed(z0)

In [ ]:
za = recArrayParsed(gu)[3]["states"]
za

In [ ]:
za

In [ ]:
m = gu.squeeze()
names = m.dtype.names
m.size

m[1][0][0,0][2].squeeze()

In [ ]:
gu.squeeze().dtype.names

In [ ]:
schema.list_tables()

In [ ]:
parsed_events = dj.create_virtual_module('bdata', 'bdata')

In [ ]:
bdata.Sessions() & "sessiondate > '2024-05-01'"

In [ ]:
sessions = dj.create_virtual_module('sessions', 'bl_bdata')

In [ ]:
(sessions.Sessions() & "sessid = 811000").fetch1("sessiondate")

In [ ]:
sessions.Sessions() & "sessiondate > '2021-01-01'" & "experimenter = 'Thomas'"

In [ ]:
mysessid = 956289

In [ ]:
import datetime

In [ ]:
ratinfo = dj.create_virtual_module('ratinfo', 'ratinfotest')

In [ ]:
ratinfo.Rats() & "experimenter = 'Thomas'"

In [ ]:

schema = dj.Schema(f"{dj.config['database.user']}_shapes") # 

@schema # 
class Rectangle(dj.Manual):
    definition = """ # (3)
    shape_id: int
    ---
    shape_height: float
    shape_width: float
    """


@schema
class Area(dj.Computed):
    definition = """
    -> Rectangle
    ---
    shape_area: float
    """
    def make(self, key):
        rectangle = (Rectangle & key).fetch1()
        Area.insert1(
            dict(
                shape_id=rectangle["shape_id"],
                shape_area=rectangle["shape_height"] * rectangle["shape_width"],
            )
        )